In [0]:
df = spark.read.parquet(f"wasbs://telematics@dln2blobdatalanding.blob.core.chinacloudapi.cn/FUEL_RANKING_R_TRIP_V4/report_date=2024060*").filter("duration = 0").select("ESN", "ReportDate", "X_AvgVehicleWeight","Trip","Delta_Dist")
df.count()

25432236

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import col, lag, expr

window_spec = Window.partitionBy("ESN","ReportDate").orderBy("Trip")
combined_df = df.withColumn("PrevWeight", lag("X_AvgVehicleWeight").over(window_spec))
combined_df = combined_df.withColumn("Prevtrip", lag("Trip").over(window_spec))
combined_df_1 = combined_df.withColumn("WeightDiff", col("X_AvgVehicleWeight") - col("PrevWeight"))
combined_df_1 = combined_df_1.withColumn("Trip_difference", col("Trip") - col("Prevtrip"))
combined_df_1.display()

ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist PrevWeight Prevtrip WeightDiff Trip_difference 4 20240602 null null null null null null null 100 20240608 null null null null null null null 123 20240601 null null null null null null null 123 20240603 null null null null null null null 123 20240608 null null null null null null null 1068 20240606 null null null null null null null 1068 20240609 null null null null null null null 1069 20240606 null null null null null null null 1853 20240603 null null null null null null null 2774 20240601 null null null null null null null 2774 20240602 null null null null null null null 4497 20240602 null null null null null null null 4497 20240605 null null null null null null null 7054 20240602 null null null null null null null 45292 20240603 null null null null null null null 45292 20240605 null null null null null null null 76734 20240602 null null null null null null null 76734 20240606 null null null null null null null 76734 20240609 null null null null null null null 537654 20240606 null null null null null null null 4120003 20240602 null null null null null null null 4120003 20240609 null null null null null null null 4120036 20240601 null null null null null null null 4120036 20240609 null null null null null null null 5516133 20240609 null null null null null null null 5997331 20240602 null null null null null null null 6156868 20240604 null null null null null null null 6156868 20240605 null null null null null null null 6156868 20240607 null null null null null null null 6528770 20240602 null null null null null null null 7635416 20240603 null null null null null null null 7647885 20240608 null null null null null null null 7653759 20240601 null null null null null null null 7653759 20240603 null null null null null null null 7682210 20240606 null null null null null null null 7685524 20240602 null null null null null null null 7685524 20240604 null null null null null null null 7695358 20240602 null null null null null null null 7731445 20240603 null null null null null null null 7741587 20240603 null null null null null null null 7744180 20240605 null null null null null null null 7744180 20240608 null null null null null null null 8027389 20240601 null null null null null null null 8027389 20240609 null null null null null null null 8135234 20240602 null null null null null null null 8237125 20240601 null null null null null null null 8237841 20240603 null null null null null null null 8970800 20240601 null null null null null null null 8970800 20240602 null null null null null null null 8970800 20240605 null null null null null null null 8970800 20240608 null null null null null null null 9005499 20240609 null null null null null null null 9552464 20240606 null null null null null null null 11152577 20240603 null null null null null null null 11152577 20240605 null null null null null null null 11152577 20240608 null null null null null null null 11152577 20240609 null null null null null null null 12000197 20240605 null null null null null null null 12000197 20240607 null null null null null null null 12000987 20240607 null null null null null null null 19027065 20240601 null null null null null null null 19027065 20240603 null null null null null null null 19030444 20240605 null null null null null null null 19070419 20240603 null null null null null null null 19070419 20240604 null null null null null null null 19070424 20240603 null null null null null null null 19070424 20240606 null null null null null null null 19070896 20240602 null null null null null null null 19070896 20240606 null null null null null null null 19070896 20240607 null null null null null null null 19070897 20240603 null null null null null null null 19070898 20240602 null null null null null null null 19070898 20240607 null null null null null null null 19070898 20240609 null null null null null null null 19071030 20240604 null null null null null null null 19071030 20240606 null null null null nul

In [0]:
combined_df_2 = combined_df_1.dropna(subset=["WeightDiff"])
combined_df_3 = combined_df_2.filter(col("WeightDiff") != 0)
combined_df_3 = combined_df_3.filter(col("Trip_difference")==1)
combined_df_3.count()

3631947

In [0]:
from pyspark.sql.functions import col, avg, stddev, lit
stats_df = combined_df_3.select(avg(col("WeightDiff")).alias("mean"), stddev(col("WeightDiff")).alias("stddev")).collect()[0]
mean = stats_df["mean"]
stddev = stats_df["stddev"]
threshold = 2 * stddev
lower_bound = mean - threshold
upper_bound = mean + threshold

print(f"Mean: {mean}, Std Dev: {stddev}, Threshold: {threshold}")
print(f"Lower Bound: {lower_bound}, Upper Bound: {upper_bound}")

combined_df_4 = combined_df_3.filter((col("WeightDiff") <= lower_bound) | (col("WeightDiff") >= upper_bound))
combined_df_4.drop(col("Trip_difference")).count()

Mean: -0.37608772760175313, Std Dev: 9.298896348906608, Threshold: 18.597792697813215
Lower Bound: -18.97388042541497, Upper Bound: 18.221704970211462


169117

In [0]:
from pyspark.sql.functions import when
#在每个Delta_distance 0-10km定义为0 10-50km定义为1 大于50km定义为2 
combined_df_5 = combined_df_4.withColumn("Delta_Dist_Label",
                   when(col("Delta_Dist") <= 10000, 0)
                   .when((col("Delta_Dist") > 10000) & (col("Delta_Dist") <= 50000), 1)
                   .otherwise(2))
combined_df_5.display(100)


ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist PrevWeight Prevtrip WeightDiff Trip_difference Delta_Dist_Label 69808536 20240602 48.12399999999999 3.0 119870.0 23.392 2.0 24.73199999999999 1.0 2 71118573 20240604 28.023999999999994 5.0 177205.0 50.094000000000015 4.0 -22.07000000000002 1.0 2 71118574 20240602 57.824000000000076 4.0 265720.0 27.711999999999996 3.0 30.11200000000008 1.0 2 71119580 20240601 23.139999999999997 7.0 17955.0 43.06000000000003 6.0 -19.920000000000034 1.0 1 71122897 20240603 24.132000000000005 7.0 238210.0 65.7239999999999 6.0 -41.5919999999999 1.0 2 71122897 20240607 34.714000000000006 2.0 147670.0 67.11599999999999 1.0 -32.40199999999998 1.0 2 71123079 20240607 41.12999999999989 2.0 600195.0 22.239999999999984 1.0 18.889999999999905 1.0 2 71124568 20240607 32.346000000000025 4.0 188495.0 60.22999999999992 3.0 -27.883999999999894 1.0 2 71124941 20240603 20.06 6.0 244325.0 39.59799999999996 5.0 -19.537999999999965 1.0 2 71126045 20240603 15.081999999999999 7.0 41070.0 36.93399999999995 6.0 -21.851999999999947 1.0 1 71126093 20240606 56.361999999999966 2.0 172340.0 37.36999999999999 1.0 18.991999999999976 1.0 2 71126122 20240602 63.74799999999999 10.0 103420.0 23.22599999999998 9.0 40.522000000000006 1.0 2 71126331 20240605 43.28799999999998 18.0 89110.0 16.904 17.0 26.383999999999983 1.0 2 71126343 20240608 73.78199999999995 3.0 88135.0 53.78999999999994 2.0 19.99200000000001 1.0 2 71126784 20240601 65.6219999999999 5.0 317170.0 40.37199999999998 4.0 25.249999999999922 1.0 2 71126784 20240601 26.929999999999975 6.0 283720.0 65.6219999999999 5.0 -38.69199999999992 1.0 2 71126784 20240607 77.20400000000005 3.0 316765.0 43.544 2.0 33.66000000000005 1.0 2 71126786 20240602 33.08 6.0 274750.0 76.11800000000002 5.0 -43.038000000000025 1.0 2 71126786 20240608 80.13600000000005 4.0 316235.0 36.885999999999996 3.0 43.25000000000006 1.0 2 71126786 20240608 33.407999999999994 5.0 284435.0 80.13600000000005 4.0 -46.72800000000006 1.0 2 71126787 20240605 13.769999999999994 4.0 6330.0 41.04399999999998 3.0 -27.273999999999987 1.0 0 71129600 20240605 17.232000000000003 13.0 8920.0 54.19 12.0 -36.958 1.0 0 71130119 20240605 41.169999999999995 9.0 68995.0 21.858 8.0 19.311999999999994 1.0 2 71130119 20240605 18.771 12.0 7255.0 38.192000000000014 11.0 -19.421000000000014 1.0 0 71130122 20240607 16.520000000000003 15.0 8040.0 48.210000000000015 14.0 -31.690000000000012 1.0 0 71130122 20240607 47.62400000000002 20.0 12450.0 26.367999999999988 19.0 21.25600000000003 1.0 1 71131374 20240608 17.403999999999993 2.0 47370.0 58.18999999999998 1.0 -40.78599999999999 1.0 1 71131819 20240609 91.53800000000004 4.0 11220.0 21.756 3.0 69.78200000000004 1.0 1 71131819 20240609 24.030000000000012 6.0 6640.0 86.64599999999997 5.0 -62.61599999999996 1.0 0 71131820 20240609 91.49000000000001 5.0 10930.0 26.45399999999999 4.0 65.03600000000002 1.0 1 71133334 20240602 37.657 4.0 9780.0 65.61399999999999 3.0 -27.956999999999994 1.0 0 76174706 20240604 59.53400000000001 19.0 7225.0 10.518000000000008 18.0 49.016000000000005 1.0 0 76193697 20240606 29.134000000000004 23.0 11150.0 10.276000000000007 22.0 18.857999999999997 1.0 1 76198450 20240603 14.848 2.0 30240.0 47.82000000000001 1.0 -32.97200000000001 1.0 1 76198450 20240603 15.824000000000014 19.0 20595.0 40.81800000000002 18.0 -24.994000000000007 1.0 1 76198752 20240602 16.246000000000006 12.0 93290.0 43.30199999999996 11.0 -27.05599999999995 1.0 2 76198752 20240608 15.888 8.0 44395.0 37.05800000000001 7.0 -21.17000000000001 1.0 1 76198752 20240608 41.11399999999998 9.0 74090.0 15.888 8.0 25.225999999999985 1.0 2 76198759 20240601 12.980000000000006 12.0 38800.0 43.00600000000004 11.0 -30.02600000000004 1.0 1 76198759 20240601 15.552000000000023 15.0 131150.0 43.81800000000002 14.0 -28.266 1.0 2 76198759 20240607 13.050000000000006 21.0 51195.0 44.13799999999998 20.0 -31.087999999999973 1.0 2 76200983 20240603 60.30799999999999 21.0 15560.0 32.47000000000002 20.0 27.837999999999973 1.0

In [0]:
#对于每个 WeightDiff进行标记 阈值是-18到18，标记[-30，-18]为-1,(18，30]为1（装货），标记[-60,-30)为-2，(30，60]为2(完成一次较重的交付)，大于-60为-3，60以上为3（完成一次大交付）
combined_df_6 = combined_df_5.withColumn("WeightDiff_Label",
                    when((col("WeightDiff") >= -30) & (col("WeightDiff") <= -18), -1)
                   .when((col("WeightDiff") > 18) & (col("WeightDiff") <= 30), 1)
                   .when((col("WeightDiff") >= -60) & (col("WeightDiff") < -30), -2)
                   .when((col("WeightDiff") > 30) & (col("WeightDiff") <= 60), 2)
                   .when(col("WeightDiff") < -60, -3)
                   .when(col("WeightDiff") > 60, 3))
result = combined_df_6.groupBy("WeightDiff_Label").count()
result.display()

WeightDiff_Label count -1 48318 1 43435 3 6055 -2 36337 2 27376 -3 7596

In [0]:
result_df = df.join(combined_df_6.select("ESN","WeightDiff_Label","Delta_Dist_Label"), on="ESN", how="left")
result_df.display()

ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist WeightDiff_Label Delta_Dist_Label 1069 20240601 null null null null null 37018224 20240601 null null null null null 41331192 20240601 null null null null null 42341502 20240601 null null null null null 42509287 20240601 null null null null null 69831627 20240601 null null null null null 71123737 20240601 null 4.0 16210.0 null null 71123737 20240601 16.253999999999998 5.0 45655.0 null null 71123737 20240601 14.89399999999999 3.0 39425.0 null null 71123737 20240601 15.004000000000005 2.0 46100.0 null null 71124935 20240601 null null null null null 71126972 20240601 23.365999999999996 9.0 63275.0 null null 71126972 20240601 33.03399999999999 1.0 60625.0 null null 71126972 20240601 55.878000000000014 12.0 103305.0 null null 71127012 20240601 null null null null null 76021004 20240601 null null null null null 76021075 20240601 null null null null null 76021237 20240601 null null null null null 76021696 20240601 null null null null null 76023194 20240601 null null null null null 76023927 20240601 null null null null null 76024679 20240601 null null null null null 76024692 20240601 null null null null null 76024915 20240601 null null null null null 76025113 20240601 null null null null null 76025399 20240601 null null null null null 76025404 20240601 null null null null null 76025582 20240601 null null null null null 76025603 20240601 null null null null null 76026102 20240601 null null null null null 76026163 20240601 null null null null null 76026503 20240601 null null null null null 76027237 20240601 null null null null null 76027430 20240601 null null null null null 76028275 20240601 null null null null null 76028633 20240601 null null null null null 76028635 20240601 null null null null null 76029402 20240601 null null null null null 76029513 20240601 null null null null null 76029554 20240601 null null null null null 76029659 20240601 null null null null null 76029809 20240601 null null null null null 76030480 20240601 null null null null null 76030646 20240601 null null null null null 76030719 20240601 null null null null null 76031045 20240601 null null null null null 76031410 20240601 null null null null null 76032804 20240601 null null null null null 76032850 20240601 null null null null null 76033235 20240601 null null null null null 76033308 20240601 null null null null null 76033415 20240601 null null null null null 76033553 20240601 null null null null null 76033922 20240601 null null null null null 76033934 20240601 null null null null null 76034102 20240601 null null null null null 76034932 20240601 null null null null null 76035012 20240601 null null null null null 76035244 20240601 null null null null null 76035606 20240601 null null null null null 76035866 20240601 null null null null null 76035873 20240601 null null null null null 76037200 20240601 null null null null null 76037349 20240601 null null null null null 76038486 20240601 null null null null null 76038545 20240601 null null null null null 76038633 20240601 null null null null null 76038783 20240601 null null null null null 76039181 20240601 null null null null null 76039880 20240601 null null null null null 76040507 20240601 null null null null null 76040599 20240601 null null null null null 76041653 20240601 null null null null null 76041676 20240601 null null null null null 76041699 20240601 null null null null null 76041769 20240601 null null null null null 76042295 20240601 2.0380000000000105 7.0 45420.0 null null 76042295 20240601 2.038000000000001 5.0 100655.0 null null 76042295 20240601 null 4.0 7770.0 null null 76042295 20240601 2.0380000000000007 6.0 124265.0 null null 76042492 20240601 null null null null null 76042554 20240601 null null null null null 76042747 20240601 null null null null null 76042765 20240601 null null null null null 76043132 20240601 null null null null null 76043566 20240601 null null null null null 76043579 20240601 null null null null null 76043829 20240601 null null nul

In [0]:
oneside= combined_df_6.filter(col("Delta_Dist_Label") == 2) \
                      .filter(col("WeightDiff_Label").isin(-2, 2,3,-3)) \
                      .drop("Trip_difference")
oneside.count()

35182

In [0]:
oneside_2= combined_df_6.filter(col("Delta_Dist_Label") == 2) \
                      .filter(col("WeightDiff_Label").isin(3,-3)) \
                      .drop("Trip_difference")
oneside_2.groupBy("ESN").agg(count("ESN").alias("count_ESN")).orderBy("count_ESN", ascending=False).display()

ESN count_ESN 77529357 13 77541571 10 77527420 10 77537822 9 76942228 8 76689372 8 76658515 8 77406064 8 77429284 7 76679922 7 76950926 7 77482724 7 77471945 7 77414527 7 77504200 7 77544700 7 76668306 7 77405945 7 76260299 7 77473266 7 77466466 6 77482760 6 76645297 6 77490658 6 76727238 6 76686480 6 77482859 6 77415394 6 77469861 6 77406065 6 76963176 6 77495149 6 76302825 6 77528180 6 77493139 6 77447599 6 76950358 6 77439404 6 77455700 6 77439271 6 77468940 6 77462292 6 76724333 6 77439338 6 76738981 6 77455475 6 77812102 6 77457441 6 76686813 6 77553431 6 82328046 6 76945021 6 76688583 6 76738076 5 76734012 5 77417055 5 82356473 5 76316632 5 77458177 5 77444452 5 77811130 5 93977174 5 77498745 5 77436505 5 77485718 5 77486008 5 76952971 5 77450230 5 76733718 5 77411377 5 76645745 5 76731431 5 77519802 5 77472117 5 82335146 5 76731704 5 77439283 5 82326774 5 77497411 5 77543546 5 77468038 5 77461650 5 77439197 5 77445629 5 77482993 5 76940896 5 76687837 5 76679702 5 77507474 5 77443912 5 77462834 5 82332098 5 76952871 5 76318500 5 77414423 5 76954913 5 77409456 5 77466437 5 77439349 5 76648987 5 77460074 5 77540882 5 77504197 5 77417396 5 77533953 5 77439341 5 77401048 5 77469625 5 77469620 5 77449987 5 77559146 5 82321268 5 77472120 5 77455452 5 77505891 5 76943916 5 76678135 5 77406432 5 77469443 5 77424036 5 76651734 5 77455730 5 76657494 5 77498734 5 77463260 5 76953302 5 77431936 5 77458955 5 77455662 5 77413594 5 77413500 5 77439442 5 77411128 5 76713475 5 77466755 4 77455683 4 77455902 4 77444385 4 77424553 4 77439114 4 76653493 4 77455513 4 76730991 4 77447365 4 77439413 4 76959375 4 77497486 4 77401194 4 76969476 4 76968326 4 77451333 4 77453481 4 77811134 4 82332221 4 77458180 4 76950368 4 76315031 4 77455687 4 77439402 4 76719403 4 82332728 4 76963577 4 77544235 4 77428255 4 77471401 4 77805040 4 76960421 4 77422463 4 77403372 4 76966310 4 77552194 4 77457959 4 77460073 4 77462352 4 77470161 4 77572128 4 77455123 4 77485011 4 77460078 4 76942536 4 76268120 4 77490454 4 77439305 4 76295256 4 82332861 4 76969969 4 77431017 4 76949749 4 76282167 4 77423828 4 77458200 4 82332268 4 76689810 4 76957258 4 77475900 4 76968345 4 76662393 4 77494564 4 76966199 4 77416161 4 77437292 4 76305447 4 76729836 4 77490597 4 77527233 4 77474755 4 77456020 4 77416993 4 77469450 4 77443254 4 82358580 4 76968467 4 77551867 4 77465965 4 76649153 4 76942330 4 76730385 4 77503965 4 76304977 4 76734647 4 76671173 4 77485020 4 77593602 4 76953953 4 77536159 4 76652515 4 76722651 4 76661484 4 76957713 4 77413532 4 77817337 4 93969042 4 77458210 4 77415654 4 77436791 4 76660889 4 77817117 4 77474039 4 77412100 4 77483032 4 77469868 4 76720195 4 77432669 4 77453480 4 77450413 4 77471307 4 76952633 4 77445515 4 77516824 4 77497098 4 77528131 4 77553534 4 76735613 4 76940001 4 77416609 4 77487578 4 77496500 4 82323578 4 77459111 4 77481507 4 77497495 4 77452388 4 76966319 4 76685315 4 77432815 4 77483612 4 76730975 4 77483595 4 77425269 4 76950046 4 77521389 4 93979372 4 77513742 4 76970888 4 77440014 4 77817731 4 77545004 4 77409468 4 77458195 4 77447375 4 77452361 4 77464454 4 77534944 4 77401376 4 77512618 4 77513566 4 77461651 4 77557241 4 76953288 4 77513696 4 76713794 4 82323681 4 77539192 4 77451403 4 77504263 4 76969029 4 77481546 4 77427005 4 77451581 4 76952626 4 77498474 4 77513923 4 77435414 4 77482031 4 76727700 4 77470157 4 77545397 4 77523144 4 76684202 4 77483343 4 77406637 4 76688267 4 77458033 3 77545164 3 77443773 3 76940207 3 76684208 3 77418257 3 77544298 3 76671431 3 77528159 3 76677325 3 77440193 3 76301142 3 76725642 3 77561278 3 77419477 3 77406787 3 76970184 3 77458151 3 82332890 3 77456884 3 77450154 3 76654526 3 77481739 3 77551055 3 77503768 3 77440013 3 93856962 3 76722464 3 76737684 3 76957117 3 77401640 3 77456607 3 77453456 3 77439286 3 76690085 3 76647502 3 77413508 3 77406075 3 76957276 3 77426339 3 77544290 3 77428995 3 77515542 3 76737642 3 76723884 3 77415196 3 77542684 3 77439798 3 77406449 3 77450761 3 7

In [0]:
oneside_2.filter(col("ESN") == "77529357").display()

ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist PrevWeight Prevtrip WeightDiff Delta_Dist_Label WeightDiff_Label 77529357 20240601 49.04300000000005 7.0 160225.0 151.05799999999994 6.0 -102.01499999999989 2 -3 77529357 20240601 35.45600000000001 11.0 87680.0 134.80999999999997 10.0 -99.35399999999996 2 -3 77529357 20240606 135.07600000000008 5.0 100925.0 29.297999999999988 4.0 105.77800000000009 2 3 77529357 20240606 50.335999999999984 6.0 91640.0 135.07600000000008 5.0 -84.7400000000001 2 -3 77529357 20240606 46.186000000000014 10.0 91615.0 128.254 9.0 -82.06799999999998 2 -3 77529357 20240606 144.05600000000007 11.0 185490.0 46.186000000000014 10.0 97.87000000000006 2 3 77529357 20240607 36.385999999999996 2.0 91085.0 119.29000000000005 1.0 -82.90400000000005 2 -3 77529357 20240607 166.306 3.0 188070.0 36.385999999999996 2.0 129.92000000000002 2 3 77529357 20240608 55.408 14.0 91440.0 118.53899999999994 13.0 -63.13099999999994 2 -3 77529357 20240608 40.356000000000016 18.0 58090.0 126.12800000000011 17.0 -85.7720000000001 2 -3 77529357 20240609 166.57800000000012 2.0 68375.0 37.918000000000006 1.0 128.6600000000001 2 3 77529357 20240609 39.473999999999975 13.0 58555.0 108.81000000000003 12.0 -69.33600000000006 2 -3 77529357 20240609 150.00199999999995 15.0 102165.0 47.288000000000025 14.0 102.71399999999993 2 3

In [0]:
oneside_2.filter(col("ESN") == "76738076").display()

ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist PrevWeight Prevtrip WeightDiff Delta_Dist_Label WeightDiff_Label 76738076 20240604 142.33599999999996 12.0 73150.0 54.83799999999997 11.0 87.49799999999999 2 3 76738076 20240604 73.44600000000003 13.0 69555.0 142.33599999999996 12.0 -68.88999999999993 2 -3 76738076 20240604 140.35200000000003 14.0 103725.0 73.44600000000003 13.0 66.906 2 3 76738076 20240605 64.6539999999999 3.0 190585.0 128.42599999999993 2.0 -63.772000000000034 2 -3 76738076 20240605 65.25599999999997 6.0 246245.0 127.30799999999995 5.0 -62.05199999999998 2 -3

In [0]:
oneside.filter(col("ESN") == "77529357").drop(col("Trip_difference")).display()

ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist PrevWeight Prevtrip WeightDiff Delta_Dist_Label WeightDiff_Label 77529357 20240601 49.04300000000005 7.0 160225.0 151.05799999999994 6.0 -102.01499999999989 2 -3 77529357 20240601 35.45600000000001 11.0 87680.0 134.80999999999997 10.0 -99.35399999999996 2 -3 77529357 20240602 168.4 4.0 52160.0 126.07999999999997 3.0 42.320000000000036 2 2 77529357 20240602 40.207999999999984 17.0 91760.0 91.65400000000002 16.0 -51.44600000000004 2 -2 77529357 20240603 33.800000000000004 2.0 91115.0 91.58400000000009 1.0 -57.784000000000084 2 -2 77529357 20240603 29.888000000000012 6.0 91430.0 64.16200000000002 5.0 -34.27400000000001 2 -2 77529357 20240603 139.13999999999993 8.0 83990.0 105.75399999999996 7.0 33.38599999999997 2 2 77529357 20240604 73.70400000000001 4.0 96405.0 36.082 3.0 37.62200000000001 2 2 77529357 20240604 29.35599999999998 5.0 91570.0 73.70400000000001 4.0 -44.34800000000003 2 -2 77529357 20240604 53.53999999999998 7.0 173970.0 88.42699999999999 6.0 -34.887000000000015 2 -2 77529357 20240606 83.69199999999998 2.0 94545.0 37.714000000000006 1.0 45.97799999999997 2 2 77529357 20240606 135.07600000000008 5.0 100925.0 29.297999999999988 4.0 105.77800000000009 2 3 77529357 20240606 50.335999999999984 6.0 91640.0 135.07600000000008 5.0 -84.7400000000001 2 -3 77529357 20240606 46.186000000000014 10.0 91615.0 128.254 9.0 -82.06799999999998 2 -3 77529357 20240606 144.05600000000007 11.0 185490.0 46.186000000000014 10.0 97.87000000000006 2 3 77529357 20240607 36.385999999999996 2.0 91085.0 119.29000000000005 1.0 -82.90400000000005 2 -3 77529357 20240607 166.306 3.0 188070.0 36.385999999999996 2.0 129.92000000000002 2 3 77529357 20240607 32.86500000000001 15.0 91425.0 82.68399999999997 14.0 -49.81899999999996 2 -2 77529357 20240608 57.38600000000003 11.0 91585.0 116.69399999999993 10.0 -59.3079999999999 2 -2 77529357 20240608 118.53899999999994 13.0 63875.0 82.61999999999998 12.0 35.91899999999997 2 2 77529357 20240608 55.408 14.0 91440.0 118.53899999999994 13.0 -63.13099999999994 2 -3 77529357 20240608 40.356000000000016 18.0 58090.0 126.12800000000011 17.0 -85.7720000000001 2 -3 77529357 20240609 166.57800000000012 2.0 68375.0 37.918000000000006 1.0 128.6600000000001 2 3 77529357 20240609 33.37 4.0 90935.0 89.33400000000005 3.0 -55.96400000000005 2 -2 77529357 20240609 68.84199999999997 5.0 98055.0 33.37 4.0 35.47199999999997 2 2 77529357 20240609 39.473999999999975 13.0 58555.0 108.81000000000003 12.0 -69.33600000000006 2 -3 77529357 20240609 150.00199999999995 15.0 102165.0 47.288000000000025 14.0 102.71399999999993 2 3

In [0]:
df.filter(col("ESN")=="77529357").display()

ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist 77529357 20240601 32.35399999999997 4.0 51405.0 77529357 20240601 50.876000000000005 8.0 11195.0 77529357 20240601 151.05799999999994 6.0 15730.0 77529357 20240601 45.59199999999999 3.0 6135.0 77529357 20240601 35.45600000000001 11.0 87680.0 77529357 20240601 49.04300000000005 7.0 160225.0 77529357 20240601 64.43400000000001 5.0 33165.0 77529357 20240601 134.80999999999997 10.0 96195.0 77529357 20240602 84.65200000000003 8.0 94200.0 77529357 20240602 40.207999999999984 17.0 91760.0 77529357 20240602 91.65400000000002 16.0 79925.0 77529357 20240602 30.06399999999997 6.0 91110.0 77529357 20240602 43.248 14.0 91695.0 77529357 20240602 158.146 19.0 9980.0 77529357 20240602 109.50100000000003 15.0 9665.0 77529357 20240602 51.14999999999998 11.0 87445.0 77529357 20240602 168.4 4.0 52160.0 77529357 20240602 126.07999999999997 3.0 41285.0 77529357 20240602 72.10199999999998 13.0 96320.0 77529357 20240603 139.13999999999993 8.0 83990.0 77529357 20240603 138.88999999999996 4.0 93715.0 77529357 20240603 105.75399999999996 7.0 7955.0 77529357 20240603 33.800000000000004 2.0 91115.0 77529357 20240603 29.888000000000012 6.0 91430.0 77529357 20240603 159.42 14.0 51370.0 77529357 20240603 64.16200000000002 5.0 7380.0 77529357 20240603 91.58400000000009 1.0 84510.0 77529357 20240603 147.04800000000017 13.0 42665.0 77529357 20240603 27.836000000000002 10.0 59345.0 77529357 20240603 44.00599999999997 11.0 33715.0 77529357 20240604 52.93000000000002 9.0 184775.0 77529357 20240604 29.35599999999998 5.0 91570.0 77529357 20240604 53.53999999999998 7.0 173970.0 77529357 20240604 36.082 3.0 91665.0 77529357 20240604 88.42699999999999 6.0 7790.0 77529357 20240604 73.70400000000001 4.0 96405.0 77529357 20240606 138.678 13.0 16665.0 77529357 20240606 29.297999999999988 4.0 87335.0 77529357 20240606 144.05600000000007 11.0 185490.0 77529357 20240606 46.186000000000014 10.0 91615.0 77529357 20240606 50.335999999999984 6.0 91640.0 77529357 20240606 37.714000000000006 1.0 61990.0 77529357 20240606 135.07600000000008 5.0 100925.0 77529357 20240606 83.69199999999998 2.0 94545.0 77529357 20240606 128.254 9.0 101000.0 77529357 20240607 36.385999999999996 2.0 91085.0 77529357 20240607 32.86500000000001 15.0 91425.0 77529357 20240607 119.29000000000005 1.0 77060.0 77529357 20240607 36.19000000000003 10.0 56885.0 77529357 20240607 166.306 3.0 188070.0 77529357 20240607 31.284000000000013 11.0 33690.0 77529357 20240607 82.68399999999997 14.0 89920.0 77529357 20240607 114.82000000000002 7.0 93455.0 77529357 20240605 57.66599999999996 10.0 59820.0 77529357 20240605 136.72400000000013 18.0 96440.0 77529357 20240605 121.76600000000003 23.0 16430.0 77529357 20240605 50.000000000000014 20.0 57535.0 77529357 20240605 50.548000000000016 11.0 31000.0 77529357 20240605 61.18400000000002 21.0 33755.0 77529357 20240605 117.81200000000001 24.0 80010.0 77529357 20240605 30.752000000000002 4.0 91155.0 77529357 20240605 135.52999999999997 8.0 91680.0 77529357 20240605 110.26200000000003 1.0 96555.0 77529357 20240605 41.32599999999999 26.0 29655.0 77529357 20240608 88.09199999999997 3.0 52990.0 77529357 20240608 55.408 14.0 91440.0 77529357 20240608 77.25199999999995 4.0 13710.0 77529357 20240608 116.69399999999993 10.0 101265.0 77529357 20240608 82.61999999999998 12.0 34315.0 77529357 20240608 126.12800000000011 17.0 91935.0 77529357 20240608 57.38600000000003 11.0 91585.0 77529357 20240608 118.53899999999994 13.0 63875.0 77529357 20240608 31.95599999999999 7.0 91060.0 77529357 20240608 93.98400000000004 5.0 23860.0 77529357 20240608 40.356000000000016 18.0 58090.0 77529357 20240609 28.02400000000001 9.0 92860.0 77529357 20240609 150.00199999999995 15.0 102165.0 77529357 20240609 68.84199999999997 5.0 98055.0 77529357 20240609 47.288000000000025 14.0 33655.0 77529357 20240609 108.81000000000003 12.0 59250.0 77529357 20240609 33.37 4.0 90935.0 77529357 20240609 39.473999999999975 13.0 58555.0 77529357 20240609 115.94400000000005 11.0

Databricks visualization. Run in Databricks to view.

In [0]:
df.filter(col("ESN")=="76733718").display()

ESN ReportDate X_AvgVehicleWeight Trip Delta_Dist 76733718 20240602 19.583999999999993 2.0 6375.0 76733718 20240603 174.22200000000004 4.0 267265.0 76733718 20240603 31.94800000000004 5.0 273985.0 76733718 20240603 30.39199999999998 6.0 237885.0 76733718 20240603 33.963999999999984 7.0 90250.0 76733718 20240603 33.964000000000034 9.0 99585.0 76733718 20240603 41.434000000000104 3.0 270985.0 76733718 20240603 33.964000000000006 8.0 12460.0 76733718 20240604 63.55199999999995 2.0 153820.0 76733718 20240606 53.14999999999998 8.0 177930.0 76733718 20240606 58.174000000000085 14.0 201040.0 76733718 20240606 50.806 13.0 177885.0 76733718 20240606 53.150000000000006 10.0 76905.0 76733718 20240606 45.538000000000004 7.0 262670.0 76733718 20240606 120.13400000000003 11.0 234045.0 76733718 20240606 53.14999999999999 9.0 18425.0 76733718 20240606 50.806000000000004 12.0 102980.0 76733718 20240605 42.444000000000045 7.0 272760.0 76733718 20240605 100.68200000000002 10.0 170910.0 76733718 20240605 null 9.0 287810.0 76733718 20240605 44.02999999999999 12.0 139480.0 76733718 20240605 61.176 4.0 82020.0 76733718 20240605 49.554000000000016 6.0 119195.0 76733718 20240605 77.63399999999999 8.0 253910.0 76733718 20240607 36.270000000000024 2.0 153810.0 76733718 20240608 40.80200000000005 4.0 272555.0 76733718 20240608 66.87399999999994 5.0 271405.0 76733718 20240608 44.81799999999998 6.0 269905.0 76733718 20240608 38.114 7.0 268895.0 76733718 20240608 60.902 3.0 202640.0 76733718 20240601 null 5.0 272895.0 76733718 20240601 100.54799999999993 4.0 203110.0 76733718 20240601 80.03400000000008 6.0 253445.0 76733718 20240601 35.41799999999999 8.0 271575.0 76733718 20240601 117.75000000000001 7.0 286790.0 76733718 20240609 null null null

Databricks visualization. Run in Databricks to view.

In [0]:
df.createOrReplaceTempView("df_table")
oneside_2.createOrReplaceTempView("oneside2_table")

In [0]:
diff_esn = spark.sql("""
SELECT ESN
FROM df_table
WHERE ESN NOT IN (SELECT ESN FROM oneside2_table)
""")

In [0]:
diff_esn.show(100)

+--------+
|     ESN|
+--------+
|    1069|
|37018224|
|41331192|
|42341502|
|42509287|
|69831627|
|71123737|
|71123737|
|71123737|
|71123737|
|71124935|
|71126972|
|71126972|
|71126972|
|71127012|
|76021004|
|76021075|
|76021237|
|76021696|
|76023194|
|76023927|
|76024679|
|76024692|
|76024915|
|76025113|
|76025399|
|76025404|
|76025582|
|76025603|
|76026102|
|76026163|
|76026503|
|76027237|
|76027430|
|76028275|
|76028633|
|76028635|
|76029402|
|76029513|
|76029554|
|76029659|
|76029809|
|76030480|
|76030646|
|76030719|
|76031045|
|76031410|
|76032804|
|76032850|
|76033235|
|76033308|
|76033415|
|76033553|
|76033922|
|76033934|
|76034102|
|76034932|
|76035012|
|76035244|
|76035606|
|76035866|
|76035873|
|76037200|
|76037349|
|76038486|
|76038545|
|76038633|
|76038783|
|76039181|
|76039880|
|76040507|
|76040599|
|76041653|
|76041676|
|76041699|
|76041769|
|76042295|
|76042295|
|76042295|
|76042295|
|76042492|
|76042554|
|76042747|
|76042765|
|76043132|
|76043566|
|76043579|
|76043829|